In [1]:
import json
# for testing I want to be able to reload my module when i change it
from importlib import reload
from subprocess import PIPE, Popen

import geopandas as gpd
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import xarray as xr
from bokeh.io import output_notebook
from bokeh.plotting import figure, show
from netCDF4 import Dataset
from shapely.geometry import LineString, Point
from sklearn.cluster import DBSCAN

import atl03_utils

atl03_utils = reload(atl03_utils)
# tells bokeh to print to notebook
output_notebook()

Loading BokehJS ...

# ATL03 - Raw Photon data 

## data downloading
ATL03 data was downloaded for several locations in the Florida Everglades and in the Florida Keys. These locations were chosen because of the availability of high-quality in-situ topobathymetric lidar data which has been collected and processed by the USGS, FEMA, and the US Army Corps of Engineers.

Of the available data variabls, the following are needed for this operation:
- dem_h - height relative to best DEM
- segment_dist_x - distance to start of segment

in addition to several others

## Photon Data Processing

### Getting the geography of tracks
To find the path of each satellite pass, all the HDF files that are present are read, the track is calculated by inspecting the individual photon returns for the maximum and minimum, and the the results are saved into a GeoDataFrame (and exported to a file)

In [2]:
# make a dataframe including all granule files in the data download folder
# alltracks = atl03_utils.make_gdf_from_ncdf_files("../data/Output*/*.h5")
# alltracks.to_file('../data/derived/all_tracks.gpkg')


In [3]:
# add OSM coastlines for reference
# gpd.read_file('../data/coastlines-split-4326/lines.shp').plot(ax=ax)



## Clustering Signal/Noise with DBSCAN

Based largely on Ma et al.

DBSCAN is a clustering algotithm based on local density of points. Its two inputs main inputs are the distance between neightbors $R_a$, and the minimum cluster size $MinPts$. Any two points that are within a distance of $R_a$ are considered neighbors. If more than $MinPts$ neighboring points are in an area, they are counted as a single cluster.

### Minimum Points
paramters can be set adaptively, from Ma et al:

> In this study, we modify the calculation process of MinPts to apply to the ICESat-2 datasets. First, the ATL03 raw data photons were used (including all photons with confidence from 0 to 4). In each ICESat-2 route that flew over the study area, every continuous 10,000 raw photons in the along-track direction were calculated together.

For this application, the minimum number of points was calculated using the method outlined in the paper above.

SN1 is calculated by:

$$SN_1 = \frac{\pi R_{\alpha}^2N_1}{hl}$$

- N1 is the number of signal and noise photons
- H is the vertical range
- l is along-track range

$$SN_2 = \frac{\pi R_{\alpha}^2N_2}{h_2 l}$$

- $N_2$ is the number of photons in the lower 5m 
- $h_2$ is the height of the 5m lowest layer = 5

$$MinPts = \frac{2SN_1 - SN_2}{\ln{2SN_1 / SN_2}}$$    

### Search distance
Ma et al. use a $R_a$ is 1.5m in daytime and 2.5m at night. However, it was found that using this search radius selected too many points that appear to be noise, and ignored signal points. Therefore, to change the search radius to prioritize horizontal neightbors, the along-track dimension is scaled down by a a factor of $H_{scale}$, so the search radius was really an ellipsoid with a minor axis of $R_a$ and a major radius of $R_a \cdot H_{scale}$

### Batch processing
Based on the methodology of Ma et al, the points are split into groups of approximately 10,000 points, in the along-track direction. The DBSCAN algorithm with the MinPts and Ra values calculated above is run. All points that are within a cluster are counted as signal, while all unclassifified points are assumed to be noise.

The beam and file to apply the algorithm to can be selcted below:

In [4]:
atl03_testfile = (
    "../data/Outputs_Boot_key/processed_ATL03_20210601225346_10561101_005_01.h5"
)
beam = atl03_utils.Beams.gt3r


In [5]:
beamdata = atl03_utils.load_beam_array_ncds(atl03_testfile, beam)

print(f"length of the dataset is {beamdata.shape[0]} points")

date = beamdata.dtype.metadata["st_date"]
print(f"This Track was flown starting at {date}")

length of the dataset is 12854 points
This Track was flown starting at 2021-06-01T22:53:46.000000Z


In [6]:
def add_track_dist_meters(strctarray):
    xcoords = strctarray["X"]
    ycoords = strctarray["Y"]
    zvals = strctarray["Z"]

    geom = [Point((x, y)) for x, y in zip(xcoords, ycoords)]

    gdf = gpd.GeoDataFrame(strctarray, geometry=geom, crs="EPSG:7912").to_crs(
        "EPSG:32617"
    )
    ymin = gdf.geometry.y.min()
    xmin = gdf.geometry.x[gdf.geometry.y.argmin()]

    dist = gdf.distance(Point(xmin, ymin))

    gdf = gdf.assign(dist_or=dist).sort_values("dist_or")
    return gdf


gdf = add_track_dist_meters(beamdata)
# gdf.to_file('../data/derived/points.gpkg')


In [7]:
TOOLS = "hover,crosshair,pan,wheel_zoom,zoom_in,zoom_out,box_zoom,undo,redo,reset,tap,save,box_select,poly_select,lasso_select,"
p = figure(tools=TOOLS, sizing_mode="scale_width", height=200)
p.scatter(gdf.dist_or.values, gdf.Z.values)
show(p)


In [8]:
# we want chunks of about 10.000 returns
nchunks = max(round(len(gdf) / 10000), 1)

# this list will be filled with geodataframes of each chunk
sndf = []

Ra = .5
# better results are found by scaling the horizontal direction down to prioritize points that are horizontally closer than others
hscale = 50
# this loop splits the dataframe into chucks of approximately 10k points, finds the adaptive minpts, does the clustering, and then assigns the results to a dataframe, which are then combined back into one big frame

for chunk in np.array_split(gdf, nchunks):
    array = chunk.to_records()

    minpts = atl03_utils.min_dbscan_points(array, Ra, hscale)
    fitarray = np.stack([array["dist_or"] / hscale, array["Z"]]).transpose()
    # for debugging
    print(f"{minpts=}")
    # run the clustering algo
    clustering = DBSCAN(eps=Ra, min_samples=minpts).fit(fitarray)

    # # move all the points and their labels into a dataframe
    df = pd.DataFrame(array).assign(cluster=clustering.labels_)
    # print(df)
    # df.cluster = df.cluster.astype("category")
    # add the signal/noise classification to the
    df["SN"] = df.cluster.apply(lambda x: "noise" if x == -1 else "signal")
    sndf.append(df)

merged = pd.concat(
    sndf,
)


seglen=4409.3936550294175,N1=12854,N2=33,h=129.59561920166016
minpts=3


In [9]:
p = figure(tools=TOOLS, sizing_mode="scale_width", height=200)
signal = merged[merged.SN == "signal"]
p.scatter(signal.dist_or.values, signal.Z.values, size=1)
show(p)


In [10]:
signal_pts = merged[merged.SN == "signal"].drop(columns="geometry")
noise_pts = merged[merged.SN == "noise"].drop(columns="geometry")

p2 = figure(
    tools=TOOLS,
    title="Signal Vs Noise identified with DBSCAN",
    sizing_mode="scale_width",
    height=200,
)
p2.scatter("dist_or", "Z", source=noise_pts, color="red")
p2.scatter("dist_or", "Z", source=signal_pts, fill_color="blue")
show(p2)


## Comparison with in-situ Topobathy

We can extract the raster values from the USGS topobathymetry data for each photon that was classified as signal 

In [11]:
def assign_na_values(inpval):
    """
    assign the appropriate value to the output of the gdallocationinfo response. '-99999' is NA as is an empty string.

    Anything else will return the input coerced to a float
    """
    if inpval in ["","-999999"]:
        return np.NaN
    else:
        return float(inpval)


In [12]:
def query_raster(dataframe, src):
    # takes a dataframe of points, and any GDAL raster as input
    xylist = dataframe[["X", "Y"]].values
    # take x,y pairs from dataframe, convert to a big string, then into a bytestring to feed into the pipe
    
    # first we take the coordinates and combine them as strings
    coordlist = "".join([f"{x} {y} " for x, y in xylist.tolist()])
    
    # convert string to a bytestring to keep GDAL happy
    pipeinput = bytes(coordlist, "utf-8")
    # gdal location info command with arguments
    cmd = ["gdallocationinfo", "-geoloc", "-valonly", src]
    # open a pipe to these commands
    with Popen(cmd, stdout=PIPE, stdin=PIPE) as p:
        # feed in our bytestring
        out, err = p.communicate(input=pipeinput)
    outlist = out.decode("utf-8").split("\n")
    # go through and assign NA values as needed. ALso discard the extra empty line that the split command induces
    cleanedlist = [assign_na_values(inpval) for inpval in outlist[:-1]]
    return cleanedlist

outlist = query_raster(signal, "../data/fl2017_usace_fema_irma_Job718945/floria.vrt")
# mangrove_heightlist = query_raster(signal,'../data/CMS_Global_Map_Mangrove_Canopy_1665/data/hmax95/height_vrt.vrt')
gebco_depth = query_raster(signal,"../data/GEBCO_05_Apr_2022_1e04da23c5ec/gebco_2021_n24.845237731933594_s24.56989288330078_w-81.18896484375001_e-80.8641815185547.tif")

# manually change gebco to approximate the same vertical reference (ie. ellipsoid instead of geoid)
geoid_adjust = -25

gebco_depth = [depth + geoid_adjust for depth in gebco_depth] 

In [13]:
signal = signal.assign(
    in_situ_height=outlist,
    # canopy_h=mangrove_heightlist,
    gebco_elev = gebco_depth
)


In [14]:
# go to a regular df since bokeh doesn't like gdf
comparison = signal.drop(columns="geometry")


In [15]:
usgs_plot = figure(
    sizing_mode="scale_width",
    height=200,
    title="USGS Topobathy Vs. ICESAT-2 photon returns",
)
usgs_plot.scatter(source=comparison, x="dist_or", y="gebco_elev", color="red",legend_label='GEBCO')
usgs_plot.scatter(source=comparison, x="dist_or", y="Z", color="green",legend_label='Detected signal photon reuturns')
usgs_plot.scatter(source=comparison, x="dist_or", y="in_situ_height", color="blue",legend_label='USGS high res topobathymetric data')
usgs_plot.xaxis.axis_label = 'Along Track Distance [m]'
usgs_plot.yaxis.axis_label = 'Height relative to ellipsoid [m]'
# usgs_plot.scatter(source=comparison,x='dist_or',y='canopy_h',color='blue')
show(usgs_plot)


## my questions

- Not all tracks are equally good - some are really noisy, some are really clean. How do we programmatically selected which tracks are higher quality. Is there a metric in the metadata that might predict cleaner bathymetric results?
- How to dynamically scale the search radius? Do we keep the 10k points and change the search radius based on the horizontal length of that chunk of 10k pts?
- how to deal with non-shore-normal tracks? coasts running north-south have basically no tracts in the cross shore direction.

## Bathymetric correction


Still not implemented, but will use formula from Parrish et al.

### Separating sea surface from seafloor

> The signal photons on sea surface and seafloor were detected using the above-mentioned method in last section. To obtain the precise water depth along ICESat-2's flight routes, the sea surface photons should be firstly discriminated against the seafloor photons. The local mean sea level Lm and the root mean square (RMS) wave height were calculated by the mean and standard deviation from the detected photons on the sea surface. All photons with the elevations lower than the local mean sea level minus 3-time RMS wave height were identified as seafloor photons.

